In [0]:
#Inner join,Outer join(left,right and full),cross join

In [0]:
%fs ls dbfs:/public/retail_db


path name size modificationTime dbfs:/public/retail_db/README.md README.md 826 1713775546547 dbfs:/public/retail_db/categories/ categories/ 0 1713775513315 dbfs:/public/retail_db/create_db.sql create_db.sql 10303495 1713775521665 dbfs:/public/retail_db/create_db_tables_pg.sql create_db_tables_pg.sql 0 1713775522407 dbfs:/public/retail_db/customers/ customers/ 0 1713775522895 dbfs:/public/retail_db/daily_revenue_result_by_pid_n_revenue_desc/ daily_revenue_result_by_pid_n_revenue_desc/ 0 0 dbfs:/public/retail_db/departments/ departments/ 0 1713775524565 dbfs:/public/retail_db/load_db_tables_pg.sql load_db_tables_pg.sql 10297392 1713775531496 dbfs:/public/retail_db/order_items/ order_items/ 0 1713775541176 dbfs:/public/retail_db/orders/ orders/ 0 1713775532043 dbfs:/public/retail_db/orders_csv_op orders_csv_op 2666678 1713775537259 dbfs:/public/retail_db/orders_json_op orders_json_op 4587915 1713775540738 dbfs:/public/retail_db/products/ products/ 0 1713775545424 dbfs:/public/retail_db/schemas.json schemas.json 4419 1713775547104

In [0]:
order_df=spark.read.csv('dbfs:/public/retail_db/orders',schema='order_id INT,order_date TIMESTAMP,order_customer_id INT,orders_state STRING')

In [0]:
order_df.show()

+--------+-------------------+-----------------+---------------+
|order_id|         order_date|order_customer_id|   orders_state|
+--------+-------------------+-----------------+---------------+
|       1|2013-07-25 00:00:00|            11599|         CLOSED|
|       2|2013-07-25 00:00:00|              256|PENDING_PAYMENT|
|       3|2013-07-25 00:00:00|            12111|       COMPLETE|
|       4|2013-07-25 00:00:00|             8827|         CLOSED|
|       5|2013-07-25 00:00:00|            11318|       COMPLETE|
|       6|2013-07-25 00:00:00|             7130|       COMPLETE|
|       7|2013-07-25 00:00:00|             4530|       COMPLETE|
|       8|2013-07-25 00:00:00|             2911|     PROCESSING|
|       9|2013-07-25 00:00:00|             5657|PENDING_PAYMENT|
|      10|2013-07-25 00:00:00|             5648|PENDING_PAYMENT|
|      11|2013-07-25 00:00:00|              918| PAYMENT_REVIEW|
|      12|2013-07-25 00:00:00|             1837|         CLOSED|
|      13|2013-07-25 00:0

In [0]:
order_items_df = spark. \
    read. \
    csv(
        'dbfs:/public/retail_db/order_items',
        schema='''
            order_item_id INT, order_item_order_id INT, order_item_product_id INT, 
            order_item_quantity INT, order_item_subtotal FLOAT, order_item_product_price FLOAT
        '''
    )

In [0]:
help(order_df.join)

Help on method join in module pyspark.sql.dataframe:

join(other: 'DataFrame', on: Union[str, List[str], pyspark.sql.column.Column, List[pyspark.sql.column.Column], NoneType] = None, how: Optional[str] = None) -> 'DataFrame' method of pyspark.sql.dataframe.DataFrame instance
    Joins with another :class:`DataFrame`, using the given join expression.
    
    .. versionadded:: 1.3.0
    
    .. versionchanged:: 3.4.0
        Supports Spark Connect.
    
    Parameters
    ----------
    other : :class:`DataFrame`
        Right side of the join
    on : str, list or :class:`Column`, optional
        a string for the join column name, a list of column names,
        a join expression (Column), or a list of Columns.
        If `on` is a string or a list of strings indicating the name of the join column(s),
        the column(s) must exist on both sides, and this performs an equi-join.
    how : str, optional
        default ``inner``. Must be one of: ``inner``, ``cross``, ``outer``,
      

In [0]:
#df1.join(df2,df1['col1']==df2['col2'])

In [0]:
#order_details_df=order_df.join(order_items_df,order_df['order_id']==order_items_df['order_item_order_id'])
order_details_df.printSchema()

root
 |-- order_id: integer (nullable = true)
 |-- order_date: timestamp (nullable = true)
 |-- order_customer_id: integer (nullable = true)
 |-- orders_state: string (nullable = true)
 |-- order_item_id: integer (nullable = true)
 |-- order_item_order_id: integer (nullable = true)
 |-- order_item_product_id: integer (nullable = true)
 |-- order_item_quantity: integer (nullable = true)
 |-- order_item_subtotal: float (nullable = true)
 |-- order_item_product_price: float (nullable = true)



In [0]:
import pyspark.sql.functions as f

In [0]:
display(order_details_df.\
    groupBy('order_item_order_id','order_date').\
        agg(f.round(f.sum('order_item_subtotal')).alias('order_revenue_by_order_id')).\
            orderBy(f.col('order_date').asc(),f.col('order_revenue_by_order_id').desc()))

order_item_order_id order_date order_revenue_by_order_id 57779 2013-07-25T00:00:00Z 1650.0 84 2013-07-25T00:00:00Z 1500.0 12 2013-07-25T00:00:00Z 1300.0 73 2013-07-25T00:00:00Z 1280.0 28 2013-07-25T00:00:00Z 1160.0 62 2013-07-25T00:00:00Z 1150.0 57764 2013-07-25T00:00:00Z 1150.0 5 2013-07-25T00:00:00Z 1130.0 57788 2013-07-25T00:00:00Z 1120.0 29 2013-07-25T00:00:00Z 1110.0 99 2013-07-25T00:00:00Z 1100.0 57757 2013-07-25T00:00:00Z 1100.0 57782 2013-07-25T00:00:00Z 1050.0 57763 2013-07-25T00:00:00Z 1030.0 57765 2013-07-25T00:00:00Z 967.0 15 2013-07-25T00:00:00Z 926.0 11 2013-07-25T00:00:00Z 920.0 57759 2013-07-25T00:00:00Z 910.0 101 2013-07-25T00:00:00Z 900.0 63 2013-07-25T00:00:00Z 900.0 20 2013-07-25T00:00:00Z 880.0 57762 2013-07-25T00:00:00Z 880.0 57778 2013-07-25T00:00:00Z 870.0 24 2013-07-25T00:00:00Z 830.0 103 2013-07-25T00:00:00Z 830.0 57768 2013-07-25T00:00:00Z 830.0 57776 2013-07-25T00:00:00Z 820.0 57785 2013-07-25T00:00:00Z 820.0 58 2013-07-25T00:00:00Z 800.0 36 2013-07-25T00:00:00Z 800.0 75 2013-07-25T00:00:00Z 780.0 67416 2013-07-25T00:00:00Z 760.0 27 2013-07-25T00:00:00Z 750.0 42 2013-07-25T00:00:00Z 740.0 94 2013-07-25T00:00:00Z 740.0 8 2013-07-25T00:00:00Z 730.0 77 2013-07-25T00:00:00Z 730.0 68691 2013-07-25T00:00:00Z 730.0 19 2013-07-25T00:00:00Z 700.0 91 2013-07-25T00:00:00Z 700.0 56 2013-07-25T00:00:00Z 700.0 4 2013-07-25T00:00:00Z 700.0 17 2013-07-25T00:00:00Z 695.0 57780 2013-07-25T00:00:00Z 690.0 66 2013-07-25T00:00:00Z 680.0 33 2013-07-25T00:00:00Z 660.0 64 2013-07-25T00:00:00Z 660.0 71 2013-07-25T00:00:00Z 660.0 10 2013-07-25T00:00:00Z 652.0 81 2013-07-25T00:00:00Z 650.0 57760 2013-07-25T00:00:00Z 650.0 61 2013-07-25T00:00:00Z 640.0 57 2013-07-25T00:00:00Z 638.0 70 2013-07-25T00:00:00Z 630.0 59 2013-07-25T00:00:00Z 620.0 9 2013-07-25T00:00:00Z 600.0 57789 2013-07-25T00:00:00Z 600.0 2 2013-07-25T00:00:00Z 580.0 7 2013-07-25T00:00:00Z 580.0 57755 2013-07-25T00:00:00Z 558.0 104 2013-07-25T00:00:00Z 550.0 100 2013-07-25T00:00:00Z 550.0 14 2013-07-25T00:00:00Z 550.0 49 2013-07-25T00:00:00Z 550.0 43 2013-07-25T00:00:00Z 530.0 96 2013-07-25T00:00:00Z 530.0 45 2013-07-25T00:00:00Z 500.0 31 2013-07-25T00:00:00Z 500.0 57781 2013-07-25T00:00:00Z 500.0 57769 2013-07-25T00:00:00Z 480.0 72 2013-07-25T00:00:00Z 464.0 18 2013-07-25T00:00:00Z 450.0 51 2013-07-25T00:00:00Z 450.0 57754 2013-07-25T00:00:00Z 440.0 50 2013-07-25T00:00:00Z 430.0 57770 2013-07-25T00:00:00Z 430.0 16 2013-07-25T00:00:00Z 420.0 44 2013-07-25T00:00:00Z 400.0 52 2013-07-25T00:00:00Z 400.0 25 2013-07-25T00:00:00Z 400.0 57784 2013-07-25T00:00:00Z 400.0 21 2013-07-25T00:00:00Z 373.0 38 2013-07-25T00:00:00Z 360.0 41 2013-07-25T00:00:00Z 328.0 23 2013-07-25T00:00:00Z 300.0 34 2013-07-25T00:00:00Z 300.0 68 2013-07-25T00:00:00Z 300.0 65 2013-07-25T00:00:00Z 300.0 1 2013-07-25T00:00:00Z 300.0 57756 2013-07-25T00:00:00Z 298.0 88 2013-07-25T00:00:00Z 280.0 57773 2013-07-25T00:00:00Z 250.0 69 2013-07-25T00:00:00Z 240.0 57771 2013-07-25T00:00:00Z 240.0 46 2013-07-25T00:00:00Z 230.0 98 2013-07-25T00:00:00Z 230.0 92 2013-07-25T00:00:00Z 200.0 39 2013-07-25T00:00:00Z 200.0 83 2013-07-25T00:00:00Z 200.0 95 2013-07-25T00:00:00Z 200.0 57783 2013-07-25T00:00:00Z 200.0 57774 2013-07-25T00:00:00Z 200.0 57786 2013-07-25T00:00:00Z 200.0 37 2013-07-25T00:00:00Z 160.0 67 2013-07-25T00:00:00Z 150.0 57758 2013-07-25T00:00:00Z 150.0 35 2013-07-25T00:00:00Z 130.0 57787 2013-07-25T00:00:00Z 130.0 13 2013-07-25T00:00:00Z 128.0 97 2013-07-25T00:00:00Z 125.0 74 2013-07-25T00:00:00Z 120.0 87 2013-07-25T00:00:00Z 120.0 48 2013-07-25T00:00:00Z 100.0 30 2013-07-25T00:00:00Z 100.0 93 2013-07-25T00:00:00Z 100.0 57777 2013-07-25T00:00:00Z 80.0 164 2013-07-26T00:00:00Z 1370.0 284 2013-07-26T00:00:00Z 1350.0 165 2013-07-26T00:00:00Z 1334.0 292 2013-07-26T00:00:00Z 1300.0 188 2013-07-26T00:00:00Z 1300.0 140 2013-07-26T00:00:00Z 1250.0 171 2013-07-26T00:00:00Z 1240.0 289 2013-07-26T00:00:00Z 1230.0 335 2013-07-26T00:00:00Z 1200.0 57793 2013-07-26T00:00:00Z 1190.0 243 2013-07-26T00:00:00Z 1180.0 

In [0]:
#from joined df we only want order_df's values

display(order_details_df.select(order_df["*"]))

order_id order_date order_customer_id orders_state 1 2013-07-25T00:00:00Z 11599 CLOSED 2 2013-07-25T00:00:00Z 256 PENDING_PAYMENT 2 2013-07-25T00:00:00Z 256 PENDING_PAYMENT 2 2013-07-25T00:00:00Z 256 PENDING_PAYMENT 4 2013-07-25T00:00:00Z 8827 CLOSED 4 2013-07-25T00:00:00Z 8827 CLOSED 4 2013-07-25T00:00:00Z 8827 CLOSED 4 2013-07-25T00:00:00Z 8827 CLOSED 5 2013-07-25T00:00:00Z 11318 COMPLETE 5 2013-07-25T00:00:00Z 11318 COMPLETE 5 2013-07-25T00:00:00Z 11318 COMPLETE 5 2013-07-25T00:00:00Z 11318 COMPLETE 5 2013-07-25T00:00:00Z 11318 COMPLETE 7 2013-07-25T00:00:00Z 4530 COMPLETE 7 2013-07-25T00:00:00Z 4530 COMPLETE 7 2013-07-25T00:00:00Z 4530 COMPLETE 8 2013-07-25T00:00:00Z 2911 PROCESSING 8 2013-07-25T00:00:00Z 2911 PROCESSING 8 2013-07-25T00:00:00Z 2911 PROCESSING 8 2013-07-25T00:00:00Z 2911 PROCESSING 9 2013-07-25T00:00:00Z 5657 PENDING_PAYMENT 9 2013-07-25T00:00:00Z 5657 PENDING_PAYMENT 9 2013-07-25T00:00:00Z 5657 PENDING_PAYMENT 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW 12 2013-07-25T00:00:00Z 1837 CLOSED 12 2013-07-25T00:00:00Z 1837 CLOSED 12 2013-07-25T00:00:00Z 1837 CLOSED 12 2013-07-25T00:00:00Z 1837 CLOSED 12 2013-07-25T00:00:00Z 1837 CLOSED 13 2013-07-25T00:00:00Z 9149 PENDING_PAYMENT 14 2013-07-25T00:00:00Z 9842 PROCESSING 14 2013-07-25T00:00:00Z 9842 PROCESSING 14 2013-07-25T00:00:00Z 9842 PROCESSING 15 2013-07-25T00:00:00Z 2568 COMPLETE 15 2013-07-25T00:00:00Z 2568 COMPLETE 15 2013-07-25T00:00:00Z 2568 COMPLETE 15 2013-07-25T00:00:00Z 2568 COMPLETE 15 2013-07-25T00:00:00Z 2568 COMPLETE 16 2013-07-25T00:00:00Z 7276 PENDING_PAYMENT 16 2013-07-25T00:00:00Z 7276 PENDING_PAYMENT 17 2013-07-25T00:00:00Z 2667 COMPLETE 17 2013-07-25T00:00:00Z 2667 COMPLETE 17 2013-07-25T00:00:00Z 2667 COMPLETE 17 2013-07-25T00:00:00Z 2667 COMPLETE 17 2013-07-25T00:00:00Z 2667 COMPLETE 18 2013-07-25T00:00:00Z 1205 CLOSED 18 2013-07-25T00:00:00Z 1205 CLOSED 18 2013-07-25T00:00:00Z 1205 CLOSED 19 2013-07-25T00:00:00Z 9488 PENDING_PAYMENT 19 2013-07-25T00:00:00Z 9488 PENDING_PAYMENT 20 2013-07-25T00:00:00Z 9198 PROCESSING 20 2013-07-25T00:00:00Z 9198 PROCESSING 20 2013-07-25T00:00:00Z 9198 PROCESSING 20 2013-07-25T00:00:00Z 9198 PROCESSING 21 2013-07-25T00:00:00Z 2711 PENDING 21 2013-07-25T00:00:00Z 2711 PENDING 21 2013-07-25T00:00:00Z 2711 PENDING 21 2013-07-25T00:00:00Z 2711 PENDING 23 2013-07-25T00:00:00Z 4367 PENDING_PAYMENT 24 2013-07-25T00:00:00Z 11441 CLOSED 24 2013-07-25T00:00:00Z 11441 CLOSED 24 2013-07-25T00:00:00Z 11441 CLOSED 24 2013-07-25T00:00:00Z 11441 CLOSED 24 2013-07-25T00:00:00Z 11441 CLOSED 25 2013-07-25T00:00:00Z 9503 CLOSED 27 2013-07-25T00:00:00Z 3241 PENDING_PAYMENT 27 2013-07-25T00:00:00Z 3241 PENDING_PAYMENT 27 2013-07-25T00:00:00Z 3241 PENDING_PAYMENT 28 2013-07-25T00:00:00Z 656 COMPLETE 28 2013-07-25T00:00:00Z 656 COMPLETE 28 2013-07-25T00:00:00Z 656 COMPLETE 28 2013-07-25T00:00:00Z 656 COMPLETE 28 2013-07-25T00:00:00Z 656 COMPLETE 29 2013-07-25T00:00:00Z 196 PROCESSING 29 2013-07-25T00:00:00Z 196 PROCESSING 29 2013-07-25T00:00:00Z 196 PROCESSING 29 2013-07-25T00:00:00Z 196 PROCESSING 29 2013-07-25T00:00:00Z 196 PROCESSING 30 2013-07-25T00:00:00Z 10039 PENDING_PAYMENT 31 2013-07-25T00:00:00Z 6983 PAYMENT_REVIEW 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT 34 2013-07-25T00:00:00Z 4189 PROCESSING 35 2013-07-25T00:00:00Z 4840 COMPLETE 36 2013-07-25T00:00:00Z 5649 PENDING 36 2013-07-25T00:00:00Z 5649 PENDING 36 2013-07-25T00:00:00Z 5649 PENDING 37 2013-07-25T00:00:00Z 5863 CLOSED 37 2013-07-25T00:0

In [0]:
#compute revenue for those which are in complete or closed status in 2014 Jan
display(order_details_df.\
    where(f.date_format('order_date','yyyy-MM')=='2014-01').
    where("orders_state IN ('COMPLETE','CLOSED')").\
    groupBy('order_item_order_id','order_date','orders_state').\
        agg(f.round(f.sum('order_item_subtotal')).alias('order_revenue_by_order_id')).\
            orderBy(f.col('order_date').asc(),f.col('order_revenue_by_order_id').desc()))

order_item_order_id order_date orders_state order_revenue_by_order_id 25948 2014-01-01T00:00:00Z COMPLETE 1700.0 25958 2014-01-01T00:00:00Z COMPLETE 1430.0 61907 2014-01-01T00:00:00Z COMPLETE 1300.0 25939 2014-01-01T00:00:00Z COMPLETE 1260.0 25913 2014-01-01T00:00:00Z COMPLETE 1160.0 25936 2014-01-01T00:00:00Z COMPLETE 1128.0 25984 2014-01-01T00:00:00Z COMPLETE 900.0 25959 2014-01-01T00:00:00Z COMPLETE 900.0 25882 2014-01-01T00:00:00Z COMPLETE 880.0 61913 2014-01-01T00:00:00Z COMPLETE 880.0 25934 2014-01-01T00:00:00Z COMPLETE 860.0 61910 2014-01-01T00:00:00Z COMPLETE 860.0 25916 2014-01-01T00:00:00Z COMPLETE 850.0 25907 2014-01-01T00:00:00Z COMPLETE 805.0 25902 2014-01-01T00:00:00Z COMPLETE 750.0 25980 2014-01-01T00:00:00Z COMPLETE 740.0 25900 2014-01-01T00:00:00Z CLOSED 720.0 25963 2014-01-01T00:00:00Z CLOSED 720.0 25920 2014-01-01T00:00:00Z COMPLETE 692.0 25897 2014-01-01T00:00:00Z COMPLETE 616.0 25901 2014-01-01T00:00:00Z COMPLETE 600.0 25895 2014-01-01T00:00:00Z COMPLETE 600.0 25970 2014-01-01T00:00:00Z COMPLETE 590.0 25969 2014-01-01T00:00:00Z COMPLETE 560.0 25932 2014-01-01T00:00:00Z CLOSED 530.0 25956 2014-01-01T00:00:00Z CLOSED 520.0 25915 2014-01-01T00:00:00Z COMPLETE 500.0 25975 2014-01-01T00:00:00Z CLOSED 500.0 61904 2014-01-01T00:00:00Z COMPLETE 500.0 25960 2014-01-01T00:00:00Z COMPLETE 495.0 25924 2014-01-01T00:00:00Z COMPLETE 490.0 25927 2014-01-01T00:00:00Z COMPLETE 484.0 25926 2014-01-01T00:00:00Z COMPLETE 400.0 25940 2014-01-01T00:00:00Z COMPLETE 400.0 61914 2014-01-01T00:00:00Z COMPLETE 400.0 25966 2014-01-01T00:00:00Z CLOSED 380.0 25891 2014-01-01T00:00:00Z CLOSED 320.0 25888 2014-01-01T00:00:00Z COMPLETE 300.0 61898 2014-01-01T00:00:00Z COMPLETE 250.0 25981 2014-01-01T00:00:00Z COMPLETE 200.0 25919 2014-01-01T00:00:00Z COMPLETE 130.0 25898 2014-01-01T00:00:00Z COMPLETE 130.0 61908 2014-01-01T00:00:00Z COMPLETE 130.0 25918 2014-01-01T00:00:00Z COMPLETE 125.0 25889 2014-01-01T00:00:00Z COMPLETE 120.0 25921 2014-01-01T00:00:00Z COMPLETE 120.0 25965 2014-01-01T00:00:00Z CLOSED 100.0 25914 2014-01-01T00:00:00Z COMPLETE 50.0 25999 2014-01-02T00:00:00Z COMPLETE 1200.0 26066 2014-01-02T00:00:00Z COMPLETE 1125.0 26061 2014-01-02T00:00:00Z COMPLETE 990.0 26050 2014-01-02T00:00:00Z COMPLETE 980.0 26037 2014-01-02T00:00:00Z COMPLETE 920.0 26034 2014-01-02T00:00:00Z COMPLETE 860.0 61920 2014-01-02T00:00:00Z COMPLETE 830.0 26009 2014-01-02T00:00:00Z COMPLETE 800.0 67973 2014-01-02T00:00:00Z COMPLETE 800.0 26040 2014-01-02T00:00:00Z COMPLETE 790.0 25991 2014-01-02T00:00:00Z CLOSED 780.0 26067 2014-01-02T00:00:00Z CLOSED 780.0 26053 2014-01-02T00:00:00Z COMPLETE 760.0 61928 2014-01-02T00:00:00Z COMPLETE 760.0 26043 2014-01-02T00:00:00Z CLOSED 700.0 26065 2014-01-02T00:00:00Z COMPLETE 665.0 26026 2014-01-02T00:00:00Z COMPLETE 600.0 25993 2014-01-02T00:00:00Z COMPLETE 600.0 26016 2014-01-02T00:00:00Z COMPLETE 590.0 61934 2014-01-02T00:00:00Z COMPLETE 520.0 26062 2014-01-02T00:00:00Z COMPLETE 500.0 61921 2014-01-02T00:00:00Z COMPLETE 500.0 61927 2014-01-02T00:00:00Z CLOSED 440.0 26070 2014-01-02T00:00:00Z CLOSED 430.0 26044 2014-01-02T00:00:00Z CLOSED 430.0 26006 2014-01-02T00:00:00Z CLOSED 400.0 61936 2014-01-02T00:00:00Z COMPLETE 400.0 26063 2014-01-02T00:00:00Z COMPLETE 396.0 26032 2014-01-02T00:00:00Z COMPLETE 384.0 26020 2014-01-02T00:00:00Z CLOSED 310.0 26049 2014-01-02T00:00:00Z COMPLETE 300.0 26056 2014-01-02T00:00:00Z COMPLETE 290.0 26041 2014-01-02T00:00:00Z COMPLETE 250.0 26004 2014-01-02T00:00:00Z COMPLETE 210.0 26023 2014-01-02T00:00:00Z COMPLETE 200.0 26013 2014-01-02T00:00:00Z COMPLETE 135.0 61924 2014-01-02T00:00:00Z COMPLETE 90.0 26036 2014-01-02T00:00:00Z COMPLETE 60.0 25990 2014-01-02T00:00:00Z CLOSED 50.0 26021 2014-01-02T00:00:00Z CLOSED 50.0 68778 2014-01-03T00:00:00Z COMPLETE 2630.0 61951 2014-01-03T00:00:00Z CLOSED 1530.0 67978 2014-01-03T00:00:00Z COMPLETE 1500.0 26096 2014-01-03T00:00:00Z CLOSED 1380.0 26287 2014-01-03T00:00:00Z CLOSED 1330.0 26263 2014-01-03T00:00:00Z COMPLETE 1325.0 26165 2014-01-0

In [0]:
#left outer join

#display(order_df.join(order_items_df,order_df['order_id']==order_items_df['order_item_order_id'],'left'))
#order_df.join(order_items_df,order_df['order_id']==order_items_df['order_item_order_id'],'left').count()
order_left_join_df=order_df.join(order_items_df,order_df['order_id']==order_items_df['order_item_order_id'],'left')

In [0]:
display(order_left_join_df.select(order_df["*"]).filter("order_item_order_id IS NULL"))

order_id order_date order_customer_id orders_state 3 2013-07-25T00:00:00Z 12111 COMPLETE 6 2013-07-25T00:00:00Z 7130 COMPLETE 22 2013-07-25T00:00:00Z 333 COMPLETE 26 2013-07-25T00:00:00Z 7562 COMPLETE 32 2013-07-25T00:00:00Z 3960 COMPLETE 40 2013-07-25T00:00:00Z 12092 PENDING_PAYMENT 47 2013-07-25T00:00:00Z 8487 PENDING_PAYMENT 53 2013-07-25T00:00:00Z 4701 PROCESSING 54 2013-07-25T00:00:00Z 10628 PENDING_PAYMENT 55 2013-07-25T00:00:00Z 2052 PENDING 60 2013-07-25T00:00:00Z 8365 PENDING_PAYMENT 76 2013-07-25T00:00:00Z 6898 COMPLETE 78 2013-07-25T00:00:00Z 8619 PAYMENT_REVIEW 79 2013-07-25T00:00:00Z 7327 PENDING_PAYMENT 80 2013-07-25T00:00:00Z 3007 COMPLETE 82 2013-07-25T00:00:00Z 3566 PENDING_PAYMENT 85 2013-07-25T00:00:00Z 1485 PENDING 86 2013-07-25T00:00:00Z 6680 PENDING_PAYMENT 89 2013-07-25T00:00:00Z 824 ON_HOLD 90 2013-07-25T00:00:00Z 9131 CLOSED 102 2013-07-25T00:00:00Z 8027 COMPLETE 108 2013-07-26T00:00:00Z 12149 PROCESSING 109 2013-07-26T00:00:00Z 9345 PENDING_PAYMENT 125 2013-07-26T00:00:00Z 4611 PENDING_PAYMENT 126 2013-07-26T00:00:00Z 610 COMPLETE 128 2013-07-26T00:00:00Z 2772 PENDING_PAYMENT 138 2013-07-26T00:00:00Z 10904 PROCESSING 144 2013-07-26T00:00:00Z 2158 PROCESSING 153 2013-07-26T00:00:00Z 8876 COMPLETE 169 2013-07-26T00:00:00Z 2611 ON_HOLD 176 2013-07-26T00:00:00Z 2897 PENDING_PAYMENT 183 2013-07-26T00:00:00Z 12105 COMPLETE 187 2013-07-26T00:00:00Z 1378 PAYMENT_REVIEW 199 2013-07-26T00:00:00Z 4608 ON_HOLD 203 2013-07-26T00:00:00Z 11791 PENDING_PAYMENT 210 2013-07-26T00:00:00Z 10102 COMPLETE 217 2013-07-26T00:00:00Z 5420 PROCESSING 218 2013-07-26T00:00:00Z 3935 COMPLETE 233 2013-07-26T00:00:00Z 12316 COMPLETE 258 2013-07-26T00:00:00Z 1137 COMPLETE 261 2013-07-26T00:00:00Z 5128 COMPLETE 270 2013-07-26T00:00:00Z 5689 COMPLETE 276 2013-07-26T00:00:00Z 2221 PENDING_PAYMENT 291 2013-07-26T00:00:00Z 5506 PROCESSING 298 2013-07-26T00:00:00Z 4967 COMPLETE 309 2013-07-26T00:00:00Z 10396 COMPLETE 310 2013-07-26T00:00:00Z 1256 COMPLETE 317 2013-07-26T00:00:00Z 1450 COMPLETE 322 2013-07-26T00:00:00Z 2864 COMPLETE 329 2013-07-26T00:00:00Z 1944 SUSPECTED_FRAUD 331 2013-07-26T00:00:00Z 4797 PENDING_PAYMENT 340 2013-07-26T00:00:00Z 7995 PENDING_PAYMENT 341 2013-07-26T00:00:00Z 10128 CLOSED 344 2013-07-26T00:00:00Z 2816 PENDING 346 2013-07-26T00:00:00Z 3646 COMPLETE 361 2013-07-27T00:00:00Z 8286 PROCESSING 369 2013-07-27T00:00:00Z 189 COMPLETE 371 2013-07-27T00:00:00Z 4428 PENDING_PAYMENT 374 2013-07-27T00:00:00Z 5906 PROCESSING 379 2013-07-27T00:00:00Z 8735 PENDING_PAYMENT 380 2013-07-27T00:00:00Z 9505 PENDING_PAYMENT 400 2013-07-27T00:00:00Z 5626 PENDING 406 2013-07-27T00:00:00Z 9023 COMPLETE 412 2013-07-27T00:00:00Z 9397 COMPLETE 420 2013-07-27T00:00:00Z 4632 COMPLETE 426 2013-07-27T00:00:00Z 10419 COMPLETE 434 2013-07-27T00:00:00Z 11390 PENDING_PAYMENT 435 2013-07-27T00:00:00Z 5719 CLOSED 439 2013-07-27T00:00:00Z 9353 COMPLETE 440 2013-07-27T00:00:00Z 7290 COMPLETE 445 2013-07-27T00:00:00Z 3859 PENDING 448 2013-07-27T00:00:00Z 7167 COMPLETE 452 2013-07-27T00:00:00Z 5128 COMPLETE 457 2013-07-27T00:00:00Z 4036 PENDING_PAYMENT 460 2013-07-27T00:00:00Z 2521 PENDING_PAYMENT 464 2013-07-27T00:00:00Z 7114 COMPLETE 469 2013-07-27T00:00:00Z 1731 PENDING 507 2013-07-27T00:00:00Z 4730 PENDING_PAYMENT 514 2013-07-28T00:00:00Z 10962 PENDING_PAYMENT 523 2013-07-28T00:00:00Z 4477 COMPLETE 533 2013-07-28T00:00:00Z 6770 COMPLETE 553 2013-07-28T00:00:00Z 7307 COMPLETE 559 2013-07-28T00:00:00Z 1944 ON_HOLD 564 2013-07-28T00:00:00Z 2216 CANCELED 566 2013-07-28T00:00:00Z 6335 CLOSED 569 2013-07-28T00:00:00Z 8532 CLOSED 570 2013-07-28T00:00:00Z 4622 PENDING 573 2013-07-28T00:00:00Z 5964 COMPLETE 574 2013-07-28T00:00:00Z 7145 PROCESSING 576 2013-07-28T00:00:00Z 7191 COMPLETE 578 2013-07-28T00:00:00Z 2529 PENDING_PAYMENT 588 2013-07-28T00:00:00Z 6348 COMPLETE 590 2013-07-28T00:00:00Z 132 PROCESSING 597 2013-07-28T00:00:00Z 11558 PENDING_PAYMENT 598 2013-07-28T00:00:00Z 11344 PENDING_PAYMENT 606 2013-07-28T00:00:00Z 1157 COMPLETE 610 2013-07-28T0